# Non Linear Schödinger (NLS) Energy

<ul id="top">
<li><a href="#Loading-packages"> 
             Loading Packages</a></li>
    
<li><a href="#Computer-properties"> 
             Computer properties</a></li>  

<li><a href="#Initial-value-problem:-NLS">
             Initial value problem: NLS</a></li>

<li><a href="#Test-solution">
             Test solution</a></li>
             
<li><a href="#Energy">
             Energy</a></li> 
             
         

</ul>  

## Loading packages

In [1]:
using OrdinaryDiffEq,DiffEqDevTools,BenchmarkTools
using IRKGaussLegendre
using Plots,LinearAlgebra
using Dates
using JLD2, FileIO

In [84]:
#plotly()

<a href="#top">Back to the top</a>

## Computer properties

In [2]:
#export JULIA_NUM_THREADS=2
Threads.nthreads()

1

In [4]:
#;cat /proc/cpuinfo # on Linux machines

In [3]:
using Hwloc
Hwloc.num_physical_cores()

2

<a href="#top">Back to the top</a>

## Initial value problem: NLS

In [2]:
include("../examples/NLS.jl")
include("../examples/InitialNLS.jl")

t0=0.0
t1=3.0
t1=30.0


u064 =InitialNLS(Float64)
tspan64=(t0,t1)
prob64 = ODEProblem(NLSODE!,u064,tspan64)

setprecision(BigFloat, 108);
u0128 =InitialNLS(BigFloat)
tspan128=(BigFloat(t0),BigFloat(t1))
prob128 = ODEProblem(NLSODE!,u0128,tspan128);
(typeof(u064),typeof(tspan64),typeof(u0128),typeof(tspan128))

(Array{Float64,1}, Tuple{Float64,Float64}, Array{BigFloat,1}, Tuple{BigFloat,BigFloat})

<a href="#top">Back to the top</a>

## Test solution

In [3]:
setprecision(BigFloat, 256)
#sol =solve(prob128,Vern9(),save_everystep=false, abstol=1e-32,reltol=1e-32);
#@save "./Data/NLS_test_solF128END.jld2" sol

@load "./Data/NLS_test_solF128END.jld2" sol
test_sol = TestSolution(sol);
sol.destats

u0256=InitialNLS(BigFloat)
E0=NLSHam(u0256,[])
(Float32(sol.t[end]),Float32(NLSHam(sol.u[end],[])/E0-1))

(3.0f0, 1.7947698f-33)

<a href="#top">Back to the top</a>

## Energy

### Float64 Computations

In [4]:
abstols = 1.0 ./ 10.0 .^ (14:17)
reltols = 1.0 ./ 10.0 .^ (14:17);
#dts=collect(3.1e-3.*(1:length(reltols)));
dts=collect(8.2e-3.*(1:length(reltols)));

In [5]:
pl=plot(title="Energy error", xlabel="t", ylabel="ΔE")
#maxE1=[]
#maxE2=[]
#maxE9=[]
for k in 1:length(abstols)
    sol9=solve(prob64,Vern9(),abstol=abstols[k],reltol=reltols[k])
    ΔE9 = map(x->NLSHam(BigFloat.(x),[]), sol9.u)./E0.-1
    sol1= solve(prob64,IRKGL16(),abstol=abstols[k],reltol=reltols[k]);
    ΔE1 = map(x->NLSHam(BigFloat.(x),[]), sol1.u)./E0.-1
    sol2= solve(prob64,IRKGL16(),adaptive=false, dt=dts[k]);
    ΔE2 = map(x->NLSHam(BigFloat.(x),[]), sol2.u)./E0.-1
    pl=plot!(sol9.t,log10.(abs.(ΔE9)), label="", color="blue")
    pl=plot!(sol1.t,log10.(abs.(ΔE1)), label="", color="red")
    pl=plot!(sol2.t,log10.(abs.(ΔE2)), label="", color="green")
#    push!(maxE1,maximum(log10.(abs.(ΔE1))))
#    push!(maxE2,maximum(log10.(abs.(ΔE2))))
#    push!(maxE9,maximum(log10.(abs.(ΔE9))))
end
plot(pl)

<a href="#top">Back to the top</a>